# Importing Libraries, Setting Path, Importing DF.

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
import os
import folium
from folium.plugins import MarkerCluster
import json
path = r'C:\Users\Chaot\Python stuff\06 - Utah Real Estate Housing Prices'
clean_cities = pd.read_csv(os.path.join(path, 'Data Brief + Data Sets', 'Utah Housing Datasets', 'cleaned_cities.csv'), index_col = False, encoding = 'utf-8')
clean_cities

zpid              city state  zipcode   latitude  longitude  \
0     2072348967    Salt Lake City    UT    84106  40.705242 -111.85947   
1       72632530  West Valley City    UT    84128  40.675503 -112.04050   
2       12815101  West Valley City    UT    84120  40.676613 -111.99914   
3       12741992  West Valley City    UT    84119  40.715977 -111.93539   
4       12738716    Salt Lake City    UT    84104  40.753315 -111.91732   
...          ...               ...   ...      ...        ...        ...   
3754   345339765  Saratoga Springs    UT    84045  40.361380 -111.90911   
3755   345339767  Saratoga Springs    UT    84045  40.361362 -111.90856   
3756   347892730  Saratoga Springs    UT    84045  40.389470 -111.93355   
3757   348419124  Saratoga Springs    UT    84045  40.398994 -111.92335   
3758  2053373356  Saratoga Springs    UT    84045  40.389130 -111.93343   

         price  bathrooms  bedrooms  living_area      home_type  zestimate  \
0     849000.0        2.0       3.0       2598.0  SINGLE_FAMILY        NaN   
1     799999.0        5.0       5.0       5131.0  SINGLE_FAMILY   797800.0   
2     510000.0        2.0       4.0       2072.0  SINGLE_FAMILY   521200.0   
3     379888.0        1.0       3.0        925.0  SINGLE_FAMILY   387700.0   
4     595000.0        2.0       3.0       2039.0  SINGLE_FAMILY   613200.0   
...        ...        ...       ...          ...            ...        ...   
3754  874990.0        3.0       5.0       4848.0  SINGLE_FAMILY   844600.0   
3755  824990.0        4.0       4.0       4806.0  SINGLE_FAMILY   817300.0   
3756  525000.0        2.0       2.0       1523.0      TOWNHOUSE   528000.0   
3757  448900.0        3.0       3.0       1570.0      TOWNHOUSE        NaN   
3758  525000.0        2.0       2.0       1523.0      TOWNHOUSE   521600.0   

     country  tax_assessed_value new_home            construction_type  \
0        USA                 NaN      NaN                          NaN   
1        USA            667700.0      NaN                          NaN   
2        USA            380400.0      NaN                          NaN   
3        USA            299100.0      NaN                          NaN   
4        USA            345300.0      NaN                          NaN   
...      ...                 ...      ...                          ...   
3754     USA                 NaN     True                 BUILDER_SPEC   
3755     USA                 NaN     True                 BUILDER_SPEC   
3756     USA                 NaN     True  NEW_CONSTRUCTION_TYPE_OTHER   
3757     USA                 NaN      NaN                          NaN   
3758     USA                 NaN     True  NEW_CONSTRUCTION_TYPE_OTHER   

                                       home_detail_link  
0     https://www.zillow.com/homedetails/1108-E-Elgi...  
1     https://www.zillow.com/homedetails/6261-W-Terr...  
2     https://www.zillow.com/homedetails/4329-S-Mign...  
3     https://www.zillow.com/homedetails/2525-S-Lest...  
4     https://www.zillow.com/homedetails/728-S-900-W...  
...                                                 ...  
3754  https://www.zillow.com/homedetails/318-E-Empir...  
3755  https://www.zillow.com/homedetails/378-E-Empir...  
3756  https://www.zillow.com/homedetails/1497-N-Sara...  
3757  https://www.zillow.com/homedetails/164-W-Harve...  
3758  https://www.zillow.com/homedetails/1481-N-Sara...  

[3759 rows x 17 columns]

In [2]:
# Changing data types for columns.
clean_cities['price'] = clean_cities['price'].astype(int)
clean_cities['bedrooms'] = clean_cities['bedrooms'].fillna(0).astype(int)
clean_cities['bathrooms'] = clean_cities['bathrooms'].fillna(0).astype(int)
clean_cities['zestimate'] = clean_cities['zestimate'].fillna(0).astype(int)
clean_cities['tax_assessed_value'] = clean_cities['tax_assessed_value'].fillna(0).astype(int)
clean_cities['new_home'] = clean_cities['new_home'].fillna(False).astype(bool)
clean_cities['living_area'] = clean_cities['living_area'].fillna(0)
clean_cities['construction_type'] = clean_cities['construction_type'].fillna('Not new home').astype(str)

In [3]:
# checking data types along with non null.
clean_cities.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3759 entries, 0 to 3758
Data columns (total 17 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   zpid                3759 non-null   int64  
 1   city                3759 non-null   object 
 2   state               3759 non-null   object 
 3   zipcode             3759 non-null   int64  
 4   latitude            3759 non-null   float64
 5   longitude           3759 non-null   float64
 6   price               3759 non-null   int32  
 7   bathrooms           3759 non-null   int32  
 8   bedrooms            3759 non-null   int32  
 9   living_area         3759 non-null   float64
 10  home_type           3759 non-null   object 
 11  zestimate           3759 non-null   int32  
 12  country             3759 non-null   object 
 13  tax_assessed_value  3759 non-null   int32  
 14  new_home            3759 non-null   bool   
 15  construction_type   3759 non-null   object 
 16  home_d

In [4]:
#Changing UT to Utah -in case I'll be using a diff geo json later that involves State.
clean_cities['state'] = clean_cities['state'].replace({'UT': 'Utah'})

# Geo Json uploads.

In [5]:
# This Geojason is for City.
city_geo = r'C:\Users\Chaot\Python stuff\06 - Utah Real Estate Housing Prices\Data Brief + Data Sets\GeoJson\ut_muni_bound.geojson'
geo_js = open(r'C:\Users\Chaot\Python stuff\06 - Utah Real Estate Housing Prices\Data Brief + Data Sets\GeoJson\ut_muni_bound.geojson', 'r')
data = json.load(geo_js)
for i in data['features']:
    print(i)

{'type': 'Feature', 'id': 1, 'geometry': {'type': 'Polygon', 'coordinates': [[[-12582256.0139, 4634659.7998], [-12582254.3997, 4635189.5141], [-12582251.6507, 4635686.0412], [-12583294.7802, 4635716.4351], [-12583295.2528, 4635886.757], [-12583295.8565, 4636101.8391], [-12583296.0953, 4636189.1404], [-12582773.7322, 4636011.2845], [-12582253.8445, 4635832.7357], [-12581747.1536, 4635674.5686], [-12581644.1812, 4635650.8937], [-12581530.3405, 4635638.4898], [-12581217.7559, 4635634.0912], [-12581219.8098, 4635697.888], [-12581220.6261, 4636216.3898], [-12581221.4434, 4636734.9174], [-12581221.8753, 4637006.6391], [-12580973.9212, 4637003.4741], [-12580716.744, 4637002.3615], [-12580716.8335, 4637239.6246], [-12580192.3809, 4637228.4867], [-12579676.3494, 4637230.592], [-12579676.5934, 4636713.9353], [-12579680.9273, 4636471.4416], [-12579802.0685, 4636209.8135], [-12579808.6002, 4636195.3478], [-12579677.385, 4636195.4749], [-12579162.0003, 4636197.9999], [-12579162.8123, 4635679.8589],

# End Geo Json Uploads.

# Creating Subsets for Plot.

In [6]:
# Select only the necessary columns and put them in a list called columns

columns = ['city','price']

In [7]:
ut_rec = clean_cities[columns]
ut_rec

city   price
0       Salt Lake City  849000
1     West Valley City  799999
2     West Valley City  510000
3     West Valley City  379888
4       Salt Lake City  595000
...                ...     ...
3754  Saratoga Springs  874990
3755  Saratoga Springs  824990
3756  Saratoga Springs  525000
3757  Saratoga Springs  448900
3758  Saratoga Springs  525000

[3759 rows x 2 columns]

In [8]:
ut_rec = ut_rec.groupby('city')['price'].median().reset_index()
ut_rec['price'] = ut_rec['price'].astype(int)
ut_rec.head()

city   price
0  American Fork  525000
1       Benjamin  899900
2      Bountiful  599220
3    Centerville  699900
4      Coalville  725000

In [9]:
ut_rec['NAME'] = ut_rec['city'].astype(str)
ut_rec = ut_rec.drop(columns = ['city'])

In [10]:
data_to_plot = ut_rec[['NAME','price']]
print(data_to_plot)

                  NAME    price
0        American Fork   525000
1             Benjamin   899900
2            Bountiful   599220
3          Centerville   699900
4            Coalville   725000
5   Cottonwood Heights   950000
6               Draper  1100000
7       Eagle Mountain   545483
8          Grantsville   549900
9                Heber  1700000
10            Herriman   682500
11             Hideout  1647200
12            Holladay   977500
13           Hyde Park   607310
14               Kamas  1103291
15           Kaysville   784450
16          Lake Point   615199
17              Layton   527450
18                Lehi   749900
19               Logan   419990
20               Magna   445000
21            Mapleton  1207995
22             Midvale   505000
23              Midway   450000
24           Millcreek   455150
25              Murray   547450
26     North Salt Lake   475000
27              Oakley  1775000
28               Ogden   426500
29                Orem   529000
30      

# Ending creating subsets to Plot.

# Creating Choropleth maps.

In [11]:
# Setup a folium map at a high-level zoom
cities = folium.Map(location=[40.5000, -111.8625], zoom_start=9, tiles ='cartodb positron')

# Choropleth maps bind Pandas Data Frames and json geometries.This allows us to quickly visualize data combinations
folium.Choropleth(
    geo_data = city_geo, 
    data = data_to_plot,
    columns = ['NAME', 'price'],
    key_on = 'feature.properties.NAME',
    fill_color="RdYlGn_r",
    fill_opacity=0.8,
    line_opacity=0.3,
    nan_fill_color='black',
    legend_name = 'Median Housing Prices by City').add_to(cities)
folium.LayerControl().add_to(cities)
cities.save('map.html')
cities

In [12]:
# Setup a folium map at a high-level zoom
map = folium.Map(location=[40.5000, -111.8625], zoom_start=6, tiles ='cartodb positron')

# Choropleth maps bind Pandas Data Frames and json geometries.This allows us to quickly visualize data combinations
folium.Choropleth(
    geo_data = city_geo, 
    data = data_to_plot,
    columns = ['NAME', 'price'],
    key_on = 'feature.properties.NAME',
    fill_color = 'BrBG',fill_opacity=0.7, line_opacity=0.3,
    legend_name = "Average Housing Prices by City").add_to(map)
folium.LayerControl().add_to(map)
folium.Marker(
    location=[40.758701, -111.876183],
    tooltip='Salt Lake City',
    popup='Average Price: $953,191',
).add_to(map)

folium.Marker(
    location=[37.095169, -113.575974],
    tooltip='Saint George',
    popup='Average Price - $897,746',
).add_to(map)
map